In [1]:
import numpy as np
import pandas as pd
import os
from random import seed
  
seed(1121)


In [2]:
data_path = '/teamspace/studios/this_studio/physionet_challenge19/physionet.org/files/challenge-2019/1.0.0/training/training_setA'

In [3]:
patient_id = sorted(os.listdir(data_path))

In [4]:
len_train = round(0.7*len(patient_id))+1
len_val = round(0.15*len(patient_id))
len_test = round(0.15*len(patient_id))
len_train + len_val + len_test == len(patient_id)

False

In [5]:
len_train

14237

In [ ]:
len_val


3051

In [7]:
len_test

3051

In [ ]:
import random
train_id = random.sample(patient_id, len_train)
val_id = random.sample(set(patient_id) - set(train_id), len_val)
test_id = set(patient_id) - set(train_id) - set(val_id)

/tmp/ipykernel_17311/2808302625.py:3: DeprecationWarning: Sampling from a set deprecated
since Python 3.9 and will be removed in a subsequent version.
  val_id = random.sample(set(patient_id) - set(train_id), len_val)


## raw split

In [9]:
data_train = '/teamspace/studios/this_studio/sepsis-prediction/raw_data/training'
data_val = '/teamspace/studios/this_studio/sepsis-prediction/raw_data/validation'
data_test = '/teamspace/studios/this_studio/sepsis-prediction/raw_data/test'

In [10]:
for p in train_id:
    df = pd.read_csv(data_path + '/' + p, sep = "|")
    df.to_csv(data_train  + p, sep='|', index = False) 

In [11]:
for p in val_id:
    df = pd.read_csv(data_path + '/' + p, sep = "|")
    df.to_csv(data_val + p, sep='|', index = False) 

In [12]:
for p in test_id:
    df = pd.read_csv(data_path + '/' + p, sep = "|")
    df.to_csv(data_test + p, sep='|', index = False)

In [15]:
import os
import shutil

# Base path (update if your base path is different)
base_path = '/teamspace/studios/this_studio/sepsis-prediction/raw_data'

# Loop through all files in raw_data
for filename in os.listdir(base_path):
    if filename.endswith('.psv'):
        src = os.path.join(base_path, filename)
        
        # Move based on prefix
        if filename.startswith('test'):
            dst_dir = os.path.join(base_path, 'test')
        elif filename.startswith('validation'):
            dst_dir = os.path.join(base_path, 'validation')
        elif filename.startswith('training'):
            dst_dir = os.path.join(base_path, 'training')
        else:
            continue  # skip anything that doesn't match

        # Ensure target directory exists
        os.makedirs(dst_dir, exist_ok=True)

        # Move file
        shutil.move(src, os.path.join(dst_dir, filename))


## Baseline

In [16]:
# function to fill missing values
def impute_missing_vals(df, attributes):

    """
    function that imputes missing values.
    
    @param df: dataframe that has missing values to be
               imputed
           attributes: list of String, attributes of dataframe
    @return df_clean: dataframe without missing values

    """
    
    """
    fill missing values by the closest values first
    ffill to fill missing values in the tail
    bfill to fill missing values in the head
    """
    # copy df
    df_clean = df.copy()
    for att in attributes:
        if df_clean[att].isnull().sum() == len(df_clean):
            df_clean[att] = df_clean[att].fillna(0)
        elif df_clean[att].isnull().sum() == len(df_clean) - 1:
            df_clean[att] = df_clean[att].ffill().bfill()
        else:
            df_clean[att] = df_clean[att].interpolate(method='nearest', limit_direction='both')
            df_clean[att] = df_clean[att].ffill().bfill()
    
    return df_clean

In [24]:
for p in patient_id:
    df = pd.read_csv(data_path + '/' + p, sep="|")
    attributes = df.columns[:-1]
    df_clean = impute_missing_vals(df, attributes)

    # ✅ Safe column drop
    columns_to_drop = ['Unit1', 'Unit2', 'EtCO2']
    df_clean = df_clean.drop(columns=[col for col in columns_to_drop if col in df_clean.columns])

    # Save the cleaned data
    if p in train_id:
        save_path = '/teamspace/studios/this_studio/sepsis-prediction/baseline/train_baseline'
    elif p in val_id:
        save_path = '/teamspace/studios/this_studio/sepsis-prediction/baseline/val_baseline'
    else:
        save_path = '/teamspace/studios/this_studio/sepsis-prediction/baseline/test_baseline'

    df_clean.to_csv(save_path + p, sep='|', index=False)
    print(f"{p} saved to {save_path}")


index.html saved to /teamspace/studios/this_studio/sepsis-prediction/baseline/train_baseline
p000001.psv saved to /teamspace/studios/this_studio/sepsis-prediction/baseline/test_baseline
p000002.psv saved to /teamspace/studios/this_studio/sepsis-prediction/baseline/train_baseline
p000003.psv saved to /teamspace/studios/this_studio/sepsis-prediction/baseline/val_baseline
p000004.psv saved to /teamspace/studios/this_studio/sepsis-prediction/baseline/val_baseline
p000005.psv saved to /teamspace/studios/this_studio/sepsis-prediction/baseline/train_baseline
p000006.psv saved to /teamspace/studios/this_studio/sepsis-prediction/baseline/test_baseline
p000007.psv saved to /teamspace/studios/this_studio/sepsis-prediction/baseline/train_baseline
p000008.psv saved to /teamspace/studios/this_studio/sepsis-prediction/baseline/train_baseline
p000009.psv saved to /teamspace/studios/this_studio/sepsis-prediction/baseline/train_baseline
p000010.psv saved to /teamspace/studios/this_studio/sepsis-predicti

In [25]:
import os
import shutil

# Base path (modify as needed)
base_path = '/teamspace/studios/this_studio/sepsis-prediction/baseline'

# Loop through all files in the baseline directory
for filename in os.listdir(base_path):
    if filename.endswith('.psv'):
        src = os.path.join(base_path, filename)

        # Determine the target folder based on the prefix
        if filename.startswith('test_baseline'):
            dst_dir = os.path.join(base_path, 'test_baseline')
        elif filename.startswith('val_baseline'):
            dst_dir = os.path.join(base_path, 'val_baseline')
        elif filename.startswith('train_baseline'):
            dst_dir = os.path.join(base_path, 'train_baseline')
        else:
            continue  # skip unrelated files

        # Ensure the destination folder exists
        os.makedirs(dst_dir, exist_ok=True)

        # Move the file
        shutil.move(src, os.path.join(dst_dir, filename))
        print(f"Moved {filename} → {dst_dir}")


Moved test_baselinep008154.psv → /teamspace/studios/this_studio/sepsis-prediction/baseline/test_baseline
Moved train_baselinep018700.psv → /teamspace/studios/this_studio/sepsis-prediction/baseline/train_baseline
Moved val_baselinep001459.psv → /teamspace/studios/this_studio/sepsis-prediction/baseline/val_baseline
Moved train_baselinep020577.psv → /teamspace/studios/this_studio/sepsis-prediction/baseline/train_baseline
Moved train_baselinep014894.psv → /teamspace/studios/this_studio/sepsis-prediction/baseline/train_baseline
Moved train_baselinep002711.psv → /teamspace/studios/this_studio/sepsis-prediction/baseline/train_baseline
Moved train_baselinep006468.psv → /teamspace/studios/this_studio/sepsis-prediction/baseline/train_baseline
Moved train_baselinep015741.psv → /teamspace/studios/this_studio/sepsis-prediction/baseline/train_baseline
Moved train_baselinep012270.psv → /teamspace/studios/this_studio/sepsis-prediction/baseline/train_baseline
Moved train_baselinep014634.psv → /teamspac

In [28]:
import os
import shutil

# Base path (update if your base path is different)
base_path = '/teamspace/studios/this_studio/sepsis-prediction/baseline'

# Loop through all files in raw_data
for filename in os.listdir(base_path):
    if filename.endswith('.psv'):
        src = os.path.join(base_path, filename)
        
        # Move based on prefix
        if filename.startswith('test_baseline'):
            dst_dir = os.path.join(base_path, 'test')
        elif filename.startswith('validation_baseline'):
            dst_dir = os.path.join(base_path, 'validation')
        elif filename.startswith('training_baseline'):
            dst_dir = os.path.join(base_path, 'training')
        else:
            continue  # skip anything that doesn't match

        # Ensure target directory exists
        os.makedirs(dst_dir, exist_ok=True)

        # Move file
        shutil.move(src, os.path.join(dst_dir, filename))

In [29]:
import os
import pandas as pd

def concatenate_psv_files(folder_path, output_csv_path):
    all_data = []

    for filename in os.listdir(folder_path):
        if filename.endswith('.psv'):
            file_path = os.path.join(folder_path, filename)

            # Read the file
            df = pd.read_csv(file_path, sep='|')

            # Extract patient ID (e.g., from test_baselinep000001.psv → p000001)
            patient_id = filename.split('baseline')[-1].replace('.psv', '')
            df['patient_id'] = patient_id

            all_data.append(df)

    # Concatenate all patient data
    final_df = pd.concat(all_data, ignore_index=True)
    final_df.to_csv(output_csv_path, sep='|', index=False)
    print(f"Saved → {output_csv_path}")

# Paths
base_dir = '/teamspace/studios/this_studio/sepsis-prediction/baseline'

concatenate_psv_files(os.path.join(base_dir, 'train_baseline'), os.path.join(base_dir, 'train_concatenate.csv'))
concatenate_psv_files(os.path.join(base_dir, 'val_baseline'), os.path.join(base_dir, 'val_concatenate.csv'))
concatenate_psv_files(os.path.join(base_dir, 'test_baseline'), os.path.join(base_dir, 'test_concatenate.csv'))


Saved → /teamspace/studios/this_studio/sepsis-prediction/baseline/train_concatenate.csv
Saved → /teamspace/studios/this_studio/sepsis-prediction/baseline/val_concatenate.csv
Saved → /teamspace/studios/this_studio/sepsis-prediction/baseline/test_concatenate.csv


In [32]:
filename = '/teamspace/studios/this_studio/sepsis-prediction/baseline/val_concatenate.csv'

with open(filename, 'r') as f:
    line_count = sum(1 for line in f)

print(f"Total lines (including header): {line_count}")
print(f"Total data rows (excluding header): {line_count - 1}")


Total lines (including header): 120121
Total data rows (excluding header): 120120
